# Build *Bacillus subtilis*

We will build an ME model from the NC_000913.2 Genbank file, the iJO1366
M model, and the complex reconstruction from iJL1678-ME

In [1]:
from __future__ import print_function, division, absolute_import

# python imports
import re
from os.path import join
from collections import defaultdict
import pickle

# third party imports
import pandas
import cobra

# COBRAme
import cobrame
from cobrame.util import building, mu, me_model_interface
from cobrame.io.json import save_json_me_model, save_reduced_json_me_model

# ECOLIme
import ecolime
from ecolime import (transcription, translation, flat_files, generics, formulas, compartments)
ecolime.__file__

'/home/jt/UCSD/bacillusme-master/ecolime/__init__.py'

## Part 1: Create minimum solveable ME-model
This will include the bare minimum representations of 
- Transcription Reactions
- Translation Reactions
- Complex Formation Reactions
- Metabolic Reactions

that still produce a working ME-model

### 1) Create Model Object and populate its global info
This includes important parameters that are used to calculate coupling 
constraints as well as organism-specific information such as peptide 
processing types

In [2]:
# Define Models
ijo_directory = join(flat_files.ecoli_files_dir, 'iYO844.json')
ijo = cobra.io.load_json_model(ijo_directory)
me = cobrame.MEModel('iYO844-ME')

# ME-models require special OptLang interface if cobrapy version >= 0.6.0
# If cannot import SymbolicParameter, assume using cobrapy
# versions <= 0.5.11
try:
    from optlang.interface import SymbolicParameter
except:
    pass
else:
    me.solver = me_model_interface

# "Translational capacity" of organism
me.global_info['kt'] = 4.5  # (in h-1)scott 2010, RNA-to-protein curve fit
me.global_info['r0'] = 0.087  # scott 2010, RNA-to-protein curve fit
me.global_info['k_deg'] = 1.0/5. * 60.0  # 1/5 1/min 60 min/h # h-1

# Molecular mass of RNA component of ribosome
me.global_info['m_rr'] = 1453. # in kDa

# Average molecular mass of an amino acid
me.global_info['m_aa'] = 109. / 1000.  # in kDa

# Proportion of RNA that is rRNA
me.global_info['f_rRNA'] = .86
me.global_info['m_nt'] = 324. / 1000.  # in kDa
me.global_info['f_mRNA'] = .02

# tRNA associated global information
me.global_info['m_tRNA'] = 25000. / 1000.  # in kDA
me.global_info['f_tRNA'] = .12

# Folding Properties
me.global_info['temperature'] = 37
me.global_info['propensity_scaling'] = .45

# DNA Replication Parameters
me.global_info['GC_fraction'] = 0.507896997096

# Define the types of biomass that will be synthesized in the model
me.add_biomass_constraints_to_model(["protein_biomass", "mRNA_biomass", "tRNA_biomass", "rRNA_biomass",
                                     "ncRNA_biomass", "DNA_biomass", "lipid_biomass", "constituent_biomass",
                                     "prosthetic_group_biomass", "peptidoglycan_biomass"])

# Define ME-model compartments
me.compartments = {"p": "Periplasm", "e": "Extra-organism", "c": "Cytosol", 
                   "im": 'Inner Membrane', 'om': "Outer Membrane", "mc": "ME-model Constraint",
                   "m": "Membrane"}

### 2) Load metabolites and build Metabolic reactions
The below reads in:
- Required 
 * **reaction_matrix.txt** (reaction matrix w/ reactions unlumped, metabolites renamed etc.)
 * **metabolites.txt** (metabolite properties)
 * **reactions.txt** (info on reversiblity, whether enzyme catalyzed etc.)
 * **m_to_me_mets.csv** (mapping of enzymes/complexes used in M-model to their ME-model compatible ID)
 * **protein_complexes.txt** (protein subunit stoichiometry of all complexes, used to identify metabolites as such)
 
It creates a new e coli M-model from this info then incorporates it into the ME-model using *add_m_model_content*. metabolites are added directly reactions are added as StoichiometricData

Metabolite types have different properties in an ME-model so enzyme complexes need added to the model as Complexes not Metabolites. Components in the E. coli M-model that are actually Complexes are compiled in *complex_list*

In [3]:
# m_model = flat_files.get_m_model()
m_model = flat_files.process_m_model(ijo, 'metabolites.txt',
                                     'm_to_me_mets.csv', 'reactions.txt',
                                     'reaction_matrix.txt',
                                     'protein_complexes.txt',
                                     defer_to_rxn_matrix=set())
m_model.reactions.EX_glc__D_e.id = 'EX_glc__D_e'
m_model.repair()
# some of the "metabolites" in iJO1366 "M" model are actually complexes. We pass those in
# so they get created as complexes, not metabolites.
complexes = flat_files.get_complex_subunit_stoichiometry(
    'protein_complexes.txt').keys()
complex_set = set(
    [i.id for i in m_model.metabolites if i.id.split('_mod_')[0] in complexes])
building.add_m_model_content(me, m_model, complex_metabolite_ids=complex_set)

/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (4fe4s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (2fe2s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (LI_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (3a1hac1p_c)


In [4]:
# This adds exchange reactions for metabolites not contained in iJO1366
# Some of these cannot be produced by the model so they are added here
exchange_list = [
    'LI_c',
    'pqq_e',
    'cs_e',
    'tl_c',
    'RNase_m5','RNase_m16','RNase_m23'] # RNAses are gaps in model

for met_id in exchange_list:
    r = cobrame.MEReaction("EX_" + met_id)
    me.add_reaction(r)
    r.reaction = met_id + " <=> "

unknown metabolite 'pqq_e' created
unknown metabolite 'cs_e' created
unknown metabolite 'tl_c' created
unknown metabolite 'RNase_m5' created
unknown metabolite 'RNase_m16' created
unknown metabolite 'RNase_m23' created


In [5]:
last = 1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

1
protein_biomass_to_biomass
protein_biomass --> biomass
2
mRNA_biomass_to_biomass
mRNA_biomass --> biomass
3
tRNA_biomass_to_biomass
tRNA_biomass --> biomass
4
rRNA_biomass_to_biomass
rRNA_biomass --> biomass
5
ncRNA_biomass_to_biomass
ncRNA_biomass --> biomass
6
DNA_biomass_to_biomass
DNA_biomass --> biomass
7
lipid_biomass_to_biomass
lipid_biomass --> biomass
8
constituent_biomass_to_biomass
constituent_biomass --> biomass
9
prosthetic_group_biomass_to_biomass
prosthetic_group_biomass --> biomass
10
peptidoglycan_biomass_to_biomass
peptidoglycan_biomass --> biomass
11
EX_2ddglcn_e
2ddglcn_e --> 
12
EX_2hxmp_e
2hxmp_e --> 
13
EX_2pg_e
2pg_e --> 
14
EX_2pglyc_e
2pglyc_e --> 
15
EX_3amba_e
3amba_e --> 
16
EX_3amp_e
3amp_e --> 
17
EX_3cmp_e
3cmp_e --> 
18
EX_3gmp_e
3gmp_e --> 
19
EX_3pg_e
3pg_e --> 
20
EX_3ump_e
3ump_e --> 
21
EX_4abut_e
4abut_e --> 
22
EX_5mtr_e
5mtr_e --> 
23
EX_6pgc_e
6pgc_e --> 
24
EX_Larab_e
Larab_e --> 
25
EX_Lcyst_e
Lcyst_e --> 
26
EX_abt__L_e
abt__L_e --> 
27
EX

### 3) Add Transcription and Translation 
The below reads in:
- Required
 * **NC_000913.2.gb** (Genbank sequence annotation)
 * **ecolime/translation.py** (codon to tRNA mapping)
- Optional
 * **TUs_from_ecocyc.txt** (TU definitions, start/stop positions, etc.)
 * **ecolime/translation.py** (dictionary of gene to frameshift mutation)
 
To construct the bare minimimum components of a transcription and translation reactions. For example, transcription reactions at this point include nucleotides and the synthesized RNAs.

In [6]:
from Bio import SeqIO
from cobrame.util import dogma

gb_filename = join(flat_files.ecoli_files_dir,'NC_000964.gb')     
gb_file = SeqIO.read(gb_filename, 'gb')
full_seq = str(gb_file.seq)

element_types={'CDS', 'rRNA','tRNA', 'ncRNA'}

frameshift_string={}
for feature in gb_file.features:
    if feature.type not in element_types or 'pseudo' in feature.qualifiers:
        continue
    bnum = feature.qualifiers["locus_tag"][0]
    seq = ''
    for location in feature.location.parts:
        left_pos = int(location.start)
        right_pos = int(location.end)
        strand = '+' if location.strand == 1 else '-'
        seq = dogma.extract_sequence(full_seq, left_pos, right_pos, strand) + seq 

In [7]:
gb_filename = join(flat_files.ecoli_files_dir,'NC_000964.gb')                                                                                    
tu_df = flat_files.get_tu_dataframe('TUs_from_bsubcyc.txt')

building.build_reactions_from_genbank(me, gb_filename, tu_df, verbose=False,
                                      frameshift_dict=translation.frameshift_dict,
                                      trna_to_codon=translation.trna_to_codon)



/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:852 UserWarning: RNA Polymerase () not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1093 UserWarning: ribosome not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1136 UserWarning: RNA_degradosome not found


In [8]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

247
transcription_TU8J2_1112_from_RpoD_mono
478 atp_c + 332 ctp_c + 328 gtp_c + 412 utp_c --> RNA_BSU_03540 + RNA_BSU_03550 + 479.80870261700005 mRNA_biomass + 1550 ppi_c
248
transcription_TU8J2_1243_from_RpoD_mono
186 atp_c + 122 ctp_c + 111 gtp_c + 154 utp_c --> RNA_BSU_23050 + 183.35422381299998 mRNA_biomass + 573 ppi_c
249
transcription_TU8J2_798_from_RpoD_mono
204 atp_c + 162 ctp_c + 116 gtp_c + 269 utp_c --> RNA_BSU_17900 + RNA_BSU_17910 + 211.50199622600002 mRNA_biomass + 751 ppi_c
250
transcription_TU8J2_569_from_RpoD_mono
812 atp_c + 820 ctp_c + 641 gtp_c + 963 utp_c --> RNA_BSU_29170 + RNA_BSU_29180 + RNA_BSU_29190 + 987.8044632220001 mRNA_biomass + 3236 ppi_c
251
transcription_TU8J2_1472_from_RpoD_mono
61 atp_c + 66 ctp_c + 47 gtp_c + 75 utp_c --> RNA_BSU_23040 + 79.159648349 mRNA_biomass + 249 ppi_c
252
transcription_TU8J2_1348_from_RpoD_mono
97 atp_c + 104 ctp_c + 106 gtp_c + 113 utp_c --> RNA_BSU_06540 + 134.43701480000001 mRNA_biomass + 420 ppi_c
253
transcription_TU8J2_

811
transcription_TU8J2_1078_from_RpoD_mono
911 atp_c + 933 ctp_c + 760 gtp_c + 1060 utp_c --> RNA_BSU_04450 + RNA_BSU_04460 + RNA_BSU_04470 + 1133.342473995 mRNA_biomass + 3664 ppi_c
812
transcription_TU8J2_302_from_RpoD_mono
143 atp_c + 231 ctp_c + 172 gtp_c + 232 utp_c --> RNA_BSU_38610 + RNA_BSU_38620 + 238.42807396999999 mRNA_biomass + 778 ppi_c
813
transcription_TU8J2_311_from_RpoD_mono
220 atp_c + 195 ctp_c + 164 gtp_c + 282 utp_c --> RNA_BSU_38430 + 274.020300881 mRNA_biomass + 861 ppi_c
814
transcription_TU8J2_1312_from_RpoD_mono
1147 atp_c + 1196 ctp_c + 1051 gtp_c + 1293 utp_c --> RNA_BSU_31540 + RNA_BSU_31550 + RNA_BSU_31560 + RNA_BSU_31570 + 1475.1340323800002 mRNA_biomass + 4687 ppi_c
815
transcription_TU8J2_533_from_RpoD_mono
464 atp_c + 352 ctp_c + 343 gtp_c + 380 utp_c --> RNA_BSU_30070 + 493.372646139 mRNA_biomass + 1539 ppi_c
816
transcription_TU8J2_632_from_RpoD_mono
340 atp_c + 389 ctp_c + 362 gtp_c + 466 utp_c --> RNA_BSU_27580 + 496.713850017 mRNA_biomass + 1557 

1311
transcription_TU8J2_459_from_RpoD_mono
523 atp_c + 471 ctp_c + 399 gtp_c + 637 utp_c --> RNA_BSU_33010 + RNA_BSU_33020 + 647.8763145739999 mRNA_biomass + 2030 ppi_c
1312
transcription_TU8J2_560_from_RpoD_mono
111 atp_c + 135 ctp_c + 108 gtp_c + 159 utp_c --> RNA_BSU_29460 + 163.186824753 mRNA_biomass + 513 ppi_c
1313
transcription_TU8J2_57_from_RpoD_mono
1334 atp_c + 1166 ctp_c + 1092 gtp_c + 1384 utp_c --> RNA_BSU_38500 + RNA_BSU_38510 + RNA_BSU_38520 + RNA_BSU_38530 + RNA_BSU_38540 + 1558.521395335 mRNA_biomass + 4976 ppi_c
1314
transcription_TU8J2_669_from_RpoD_mono
1162 atp_c + 958 ctp_c + 761 gtp_c + 1310 utp_c --> RNA_BSU_24660 + RNA_BSU_24670 + RNA_BSU_24680 + RNA_BSU_24690 + RNA_BSU_24700 + RNA_BSU_24710 + RNA_BSU_24720 + RNA_BSU_24730 + 1292.596789979 mRNA_biomass + 4191 ppi_c
1315
transcription_TU8J2_79_from_RpoD_mono
118 atp_c + 69 ctp_c + 80 gtp_c + 126 utp_c --> RNA_BSU_17970 + 125.701029653 mRNA_biomass + 393 ppi_c
1316
transcription_TU8J2_891_from_RpoD_mono
320 atp_

538 atp_c + 576 ctp_c + 583 gtp_c + 793 utp_c --> RNA_BSU_06140 + 794.43177307 mRNA_biomass + 2490 ppi_c
1811
transcription_TU8J2_1404_from_RpoD_mono
352 atp_c + 212 ctp_c + 212 gtp_c + 247 utp_c --> RNA_BSU_13520 + 328.354326243 mRNA_biomass + 1023 ppi_c
1812
transcription_TU8J2_738_from_RpoD_mono
58 atp_c + 54 ctp_c + 48 gtp_c + 98 utp_c --> RNA_BSU_22020 + 81.88780753799999 mRNA_biomass + 258 ppi_c
1813
transcription_TU8J2_51_from_RpoD_mono
615 atp_c + 625 ctp_c + 467 gtp_c + 748 utp_c --> RNA_BSU_29100 + RNA_BSU_29110 + 783.434859243 mRNA_biomass + 2455 ppi_c
1814
transcription_TU8J2_2968_from_RpoD_mono
744 atp_c + 873 ctp_c + 718 gtp_c + 951 utp_c --> RNA_BSU_32240 + RNA_BSU_32250 + RNA_BSU_32260 + 1048.6094999309998 mRNA_biomass + 3286 ppi_c
1815
transcription_TU8J2_129_from_RpoD_mono
480 atp_c + 440 ctp_c + 451 gtp_c + 563 utp_c --> RNA_BSU_10670 + RNA_BSU_10680 + RNA_BSU_10690 + RNA_BSU_10700 + RNA_BSU_10710 + RNA_BSU_10720 + 598.872345892 mRNA_biomass + 1934 ppi_c
1816
transcr

0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_BSU_00190 + 2.52838134430727*(mu + 0.3915)/mu atp_c + 2.52838134430727*(mu + 0.3915)/mu h2o_c + met__L_c --> 2.52838134430727*(mu + 0.3915)/mu adp_c + 2.45810699588477*(mu + 0.3915)/mu amp_c + 2.40427983539095*(mu + 0.3915)/mu cmp_c + 2.00356652949246*(mu + 0.3915)/mu gmp_c + 2.52838134430727*(mu + 0.3915)/mu h_c + 2.52838134430727*(mu + 0.3915)/mu pi_c + protein_BSU_00190 + 0.14921134 protein_biomass + 3.25355281207133*(mu + 0.3915)/mu ump_c
1878
transcription_TU_BSU_00190
411 atp_c + 402 ctp_c + 335 gtp_c + 544 utp_c --> RNA_BSU_00190 + 538.479159932 mRNA_biomass + 1692 ppi_c
1879
translation_BSU_00200
0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_BSU_00200 + 0.482949245541838*(mu + 0.3915)/mu atp_c + 0.482949245541838*(mu + 0.3915)/mu h2o_c + met__L_c --> 0.482949245541838*(mu + 0.3915)/mu adp_c + 0.412674897119342*(mu + 0.3915)/mu amp_c + 0.490425240

...

RNA_BSU_02520 + 293.466542961 mRNA_biomass --> 
9789
DM_RNA_BSU_02470
RNA_BSU_02470 + 467.510957607 mRNA_biomass --> 
9790
DM_RNA_BSU_02460
RNA_BSU_02460 + 295.594203487 mRNA_biomass --> 
9791
DM_RNA_BSU_02480
RNA_BSU_02480 + 439.21564186800003 mRNA_biomass --> 
9792
DM_RNA_BSU_36600
RNA_BSU_36600 + 245.89253739400002 mRNA_biomass --> 
9793
DM_RNA_BSU_28200
RNA_BSU_28200 + 739.029897945 mRNA_biomass --> 
9794
DM_RNA_BSU_28190
RNA_BSU_28190 + 186.670895468 mRNA_biomass --> 
9795
DM_RNA_BSU_02730
RNA_BSU_02730 + 306.03149495699995 mRNA_biomass --> 
9796
DM_RNA_BSU_09490
RNA_BSU_09490 + 136.48807058900002 mRNA_biomass --> 
9797
DM_RNA_BSU_07360
RNA_BSU_07360 + 274.253238581 mRNA_biomass --> 
9798
DM_RNA_BSU_07350
RNA_BSU_07350 + 464.56004661799994 mRNA_biomass --> 
9799
DM_RNA_BSU_10010
RNA_BSU_10010 + 166.818129819 mRNA_biomass --> 
9800
DM_RNA_BSU_12100
RNA_BSU_12100 + 445.5759712039999 mRNA_biomass --> 
9801
DM_RNA_BSU_tRNA_20
RNA_BSU_tRNA_20 + 24.425912196000002 tRNA_biomass --> 
9802

RNA_BSU_20520 + 47.77595203 mRNA_biomass --> 
10444
DM_RNA_BSU_03710
RNA_BSU_03710 + 389.134071944 mRNA_biomass --> 
10445
DM_RNA_BSU_03720
RNA_BSU_03720 + 358.997355882 mRNA_biomass --> 
10446
DM_RNA_BSU_03700
RNA_BSU_03700 + 521.757683035 mRNA_biomass --> 
10447
DM_RNA_BSU_11260
RNA_BSU_11260 + 57.31605468000001 mRNA_biomass --> 
10448
DM_RNA_BSU_37750
RNA_BSU_37750 + 396.942334999 mRNA_biomass --> 
10449
DM_RNA_BSU_24770
RNA_BSU_24770 + 120.90969034100002 mRNA_biomass --> 
10450
DM_RNA_BSU_05290
RNA_BSU_05290 + 122.891085927 mRNA_biomass --> 
10451
DM_RNA_BSU_03610
RNA_BSU_03610 + 256.260545387 mRNA_biomass --> 
10452
DM_RNA_BSU_03600
RNA_BSU_03600 + 226.993360805 mRNA_biomass --> 
10453
DM_RNA_BSU_03590
RNA_BSU_03590 + 237.399929144 mRNA_biomass --> 
10454
DM_RNA_BSU_00090
RNA_BSU_00090 + 467.02001420700003 mRNA_biomass --> 
10455
DM_RNA_BSU_36590
RNA_BSU_36590 + 463.300553209 mRNA_biomass --> 
10456
DM_RNA_BSU_29220
RNA_BSU_29220 + 392.769690073 mRNA_biomass --> 
10457
DM_RNA_BSU_

DM_RNA_BSU_07870
RNA_BSU_07870 + 68.653450956 mRNA_biomass --> 
11111
DM_RNA_BSU_08029
RNA_BSU_08029 + 84.948086387 mRNA_biomass --> 
11112
DM_RNA_BSU_08310
RNA_BSU_08310 + 298.188305316 mRNA_biomass --> 
11113
DM_RNA_BSU_08320
RNA_BSU_08320 + 379.89668875100006 mRNA_biomass --> 
11114
DM_RNA_BSU_08330
RNA_BSU_08330 + 370.040667938 mRNA_biomass --> 
11115
DM_RNA_BSU_08560
RNA_BSU_08560 + 85.83312169 mRNA_biomass --> 
11116
DM_RNA_BSU_08670
RNA_BSU_08670 + 109.475607345 mRNA_biomass --> 
11117
DM_RNA_BSU_08680
RNA_BSU_08680 + 169.027244851 mRNA_biomass --> 
11118
DM_RNA_BSU_08690
RNA_BSU_08690 + 556.1782268430001 mRNA_biomass --> 
11119
DM_RNA_BSU_08700
RNA_BSU_08700 + 338.864429802 mRNA_biomass --> 
11120
DM_RNA_BSU_08710
RNA_BSU_08710 + 411.3819892099999 mRNA_biomass --> 
11121
DM_RNA_BSU_08720
RNA_BSU_08720 + 150.307316894 mRNA_biomass --> 
11122
DM_RNA_BSU_08750
RNA_BSU_08750 + 281.99320290500003 mRNA_biomass --> 
11123
DM_RNA_BSU_rRNA_22
RNA_BSU_rRNA_22 + 495.546177415 rRNA_biomass

RNA_BSU_21409 + 69.79032085899999 mRNA_biomass --> 
11777
DM_RNA_BSU_21410
RNA_BSU_21410 + 352.314618224 mRNA_biomass --> 
11778
DM_RNA_BSU_21420
RNA_BSU_21420 + 67.44787083300001 mRNA_biomass --> 
11779
DM_RNA_BSU_21430
RNA_BSU_21430 + 84.88959412700001 mRNA_biomass --> 
11780
DM_RNA_BSU_21490
RNA_BSU_21490 + 101.107180458 mRNA_biomass --> 
11781
DM_RNA_BSU_21530
RNA_BSU_21530 + 113.23863545700002 mRNA_biomass --> 
11782
DM_RNA_BSU_21540
RNA_BSU_21540 + 149.073046988 mRNA_biomass --> 
11783
DM_RNA_BSU_21546
RNA_BSU_21546 + 37.128906357 mRNA_biomass --> 
11784
DM_RNA_BSU_21550
RNA_BSU_21550 + 169.602798974 mRNA_biomass --> 
11785
DM_RNA_BSU_21560
RNA_BSU_21560 + 183.621379439 mRNA_biomass --> 
11786
DM_RNA_BSU_21570
RNA_BSU_21570 + 157.921971538 mRNA_biomass --> 
11787
DM_RNA_BSU_21580
RNA_BSU_21580 + 543.5020425560001 mRNA_biomass --> 
11788
DM_RNA_BSU_21590
RNA_BSU_21590 + 177.430216018 mRNA_biomass --> 
11789
DM_RNA_BSU_21600
RNA_BSU_21600 + 340.843855854 mRNA_biomass --> 
11790
DM_

DM_RNA_BSU_40710
RNA_BSU_40710 + 143.090048653 mRNA_biomass --> 
12444
DM_RNA_BSU_40750
RNA_BSU_40750 + 113.476656937 mRNA_biomass --> 
12445
DM_RNA_BSU_40760
RNA_BSU_40760 + 179.55713134700002 mRNA_biomass --> 
12446
DM_RNA_BSU_40800
RNA_BSU_40800 + 131.994044117 mRNA_biomass --> 
12447
DM_RNA_BSU_40810
RNA_BSU_40810 + 293.51001771800003 mRNA_biomass --> 
12448
DM_RNA_BSU_40850
RNA_BSU_40850 + 176.55184371500002 mRNA_biomass --> 
12449
DM_RNA_BSU_40860
RNA_BSU_40860 + 120.733051441 mRNA_biomass --> 
12450
DM_RNA_BSU_40930
RNA_BSU_40930 + 637.523747404 mRNA_biomass --> 
12451
DM_RNA_BSU_40939
RNA_BSU_40939 + 65.433632527 mRNA_biomass --> 
12452
DM_RNA_BSU_41050
RNA_BSU_41050 + 111.34047921099999 mRNA_biomass --> 


### 4) Add in complex Formation without modifications (for now)

The below reads in:
- Required
 * **protein_complexes.txt** (Metabolic complexes' protein subunit stoichiometries)
 * **protein_modification.txt** (Type and number of modifications for each protein)

In [10]:
# complex_stoichiometry_dict is a dict of {'complex_id': [{'bnum' : count}]}
rna_components = {} # component id should have 'RNA_ instead' of 'protein_'
# get Metabolic Complex composition from ECOLIme
complex_stoichiometry_dict = flat_files.get_complex_subunit_stoichiometry('protein_complexes.txt', rna_components)
# add complexes to model
complex_modification_dict = flat_files.get_complex_modifications('protein_modification.txt', 'protein_complexes.txt')
building.add_model_complexes(me, complex_stoichiometry_dict, complex_modification_dict, verbose=False)

# remove modifications. they will be added back in later
for data in me.complex_data:
    data.subreactions = {}
    
# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

Created <TranslatedGene protein_BSU20250 at 0x7f92feb71a58> in <ComplexFormation formation_BSU20250-MONOMER at 0x7f92feb718d0>
Created <TranslatedGene protein_BSU32170 at 0x7f92feb712e8> in <ComplexFormation formation_BSU32170-MONOMER at 0x7f92feb71a90>
Created <TranslatedGene protein_BSU33900 at 0x7f92feb713c8> in <ComplexFormation formation_BSU33900-MONOMER at 0x7f92feb71748>
Created <TranslatedGene protein_BSU25500 at 0x7f92feb71518> in <ComplexFormation formation_BSU25500-MONOMER at 0x7f92feb71470>
Created <TranslatedGene protein_BSU34790 at 0x7f92ff0a2ef0> in <ComplexFormation formation_BSU34790-MONOMER at 0x7f92feb71240>
Created <TranslatedGene protein_BSU00680 at 0x7f92ff0a2f28> in <ComplexFormation formation_BSU00680-MONOMER at 0x7f92ff0a2fd0>
Created <TranslatedGene protein_BSU13120 at 0x7f92ff0a29b0> in <ComplexFormation formation_BSU13120-MONOMER at 0x7f92ff0a25c0>
Created <TranslatedGene protein_BSU30230 at 0x7f92ff0a2b38> in <ComplexFormation formation_BSU30230-MONOMER at 

Created <TranslatedGene protein_BSU16780 at 0x7f92fec3e860> in <ComplexFormation formation_CPLX8J2-39 at 0x7f92fec3eef0>
Created <TranslatedGene protein_BSU14530 at 0x7f92fec3eb00> in <ComplexFormation formation_CPLX8J2-39 at 0x7f92fec3eef0>
Created <TranslatedGene protein_BSU28080 at 0x7f92fec3e320> in <ComplexFormation formation_BSU28080-MONOMER at 0x7f92fec3e9e8>
Created <TranslatedGene protein_BSU35930 at 0x7f92fec3e400> in <ComplexFormation formation_CPLX8J2-64 at 0x7f92fec3e7f0>
Created <TranslatedGene protein_BSU35940 at 0x7f92fec3e358> in <ComplexFormation formation_CPLX8J2-64 at 0x7f92fec3e7f0>
Created <TranslatedGene protein_BSU35950 at 0x7f92fec3e0f0> in <ComplexFormation formation_CPLX8J2-64 at 0x7f92fec3e7f0>
Created <TranslatedGene protein_BSU35960 at 0x7f92fec3e3c8> in <ComplexFormation formation_CPLX8J2-64 at 0x7f92fec3e7f0>
Created <TranslatedGene protein_BSU22470 at 0x7f92fec3e160> in <ComplexFormation formation_BSU22470-MONOMER at 0x7f92fec3e470>
Created <TranslatedG

Created <TranslatedGene protein_BSU22630 at 0x7f92fedfab38> in <ComplexFormation formation_CPLX8J2-19 at 0x7f92fedfa978>
Created <TranslatedGene protein_BSU22640 at 0x7f92fedfabe0> in <ComplexFormation formation_CPLX8J2-19 at 0x7f92fedfa978>
Created <TranslatedGene protein_BSU24120 at 0x7f92fedfa400> in <ComplexFormation formation_BSU24120-MONOMER at 0x7f92fedfa128>
Created <TranslatedGene protein_BSU13040 at 0x7f92fedfa160> in <ComplexFormation formation_BSU13040-MONOMER at 0x7f92fedfa438>
Created <TranslatedGene protein_BSU16570 at 0x7f92ff164cc0> in <ComplexFormation formation_BSU16570-MONOMER at 0x7f92ff164c88>
Created <TranslatedGene protein_BSU28790 at 0x7f92ff164eb8> in <ComplexFormation formation_BSU28790-MONOMER at 0x7f92ff164d30>
Created <TranslatedGene protein_BSU04010 at 0x7f92ff164c18> in <ComplexFormation formation_BSU04010-MONOMER at 0x7f92ff164fd0>
Created <TranslatedGene protein_BSU18040 at 0x7f92ff1647b8> in <ComplexFormation formation_BSU18040-MONOMER at 0x7f92ff1647

In [11]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

12453
formation_BSU20250-MONOMER
protein_BSU20250 --> BSU20250-MONOMER
12454
formation_BSU32170-MONOMER
protein_BSU32170 --> BSU32170-MONOMER
12455
formation_BSU33900-MONOMER
protein_BSU33900 --> BSU33900-MONOMER
12456
formation_BSU25500-MONOMER
protein_BSU25500 --> BSU25500-MONOMER
12457
formation_BSU34790-MONOMER
protein_BSU34790 --> BSU34790-MONOMER
12458
formation_BSU00680-MONOMER
protein_BSU00680 --> BSU00680-MONOMER
12459
formation_BSU13120-MONOMER
protein_BSU13120 --> BSU13120-MONOMER
12460
formation_BSU30230-MONOMER
protein_BSU30230 --> BSU30230-MONOMER
12461
formation_BSU12300-MONOMER
protein_BSU12300 --> BSU12300-MONOMER
12462
formation_BSU14390-MONOMER
protein_BSU14390 --> BSU14390-MONOMER
12463
formation_BSU09570-MONOMER
protein_BSU09570 --> BSU09570-MONOMER
12464
formation_BSU28620-MONOMER
protein_BSU28620 --> BSU28620-MONOMER
12465
formation_BSU29970-MONOMER
protein_BSU29970 --> BSU29970-MONOMER
12466
formation_BSU34560-MONOMER
protein_BSU34560 --> BSU34560-MONOMER
12467


12659
formation_CPLX8J2-181
protein_BSU23070 --> CPLX8J2-181
12660
formation_CPLX8J2-195
protein_BSU23850 --> CPLX8J2-195
12661
formation_BSU24060-MONOMER
protein_BSU24060 --> BSU24060-MONOMER
12662
formation_BSU28390-MONOMER
protein_BSU28390 --> BSU28390-MONOMER
12663
formation_BSU22140-MONOMER
protein_BSU22140 --> BSU22140-MONOMER
12664
formation_BSU34450-MONOMER
protein_BSU34450 --> BSU34450-MONOMER
12665
formation_BSU27390-MONOMER
protein_BSU27390 --> BSU27390-MONOMER
12666
formation_BSU32450-MONOMER
protein_BSU32450 --> BSU32450-MONOMER
12667
formation_BSU15020-MONOMER
protein_BSU15020 --> BSU15020-MONOMER
12668
formation_BSU18470-MONOMER
protein_BSU18470 --> BSU18470-MONOMER
12669
formation_CPLX8J2-97
protein_BSU35030 --> CPLX8J2-97
12670
formation_BSU08030-MONOMER
protein_BSU08030 --> BSU08030-MONOMER
12671
formation_BSU00280-MONOMER
protein_BSU00280 --> BSU00280-MONOMER
12672
formation_CPLX8J2-110
protein_BSU08340 --> CPLX8J2-110
12673
formation_CPLX8J2-6
protein_BSU15510 + pro

formation_BSU03640-MONOMER
protein_BSU03640 --> BSU03640-MONOMER
12993
formation_BSU22440-MONOMER
protein_BSU22440 --> BSU22440-MONOMER
12994
formation_BSU13580-MONOMER
protein_BSU13580 --> BSU13580-MONOMER
12995
formation_CPLX8J2-31
protein_BSU30960 + protein_BSU30970 --> CPLX8J2-31
12996
formation_BSU34390-MONOMER
protein_BSU34390 --> BSU34390-MONOMER
12997
formation_CPLX8J2-25
protein_BSU36850 + protein_BSU36860 + protein_BSU36870 --> CPLX8J2-25
12998
formation_BSU15430-MONOMER
protein_BSU15430 --> BSU15430-MONOMER
12999
formation_BSU25310-MONOMER
protein_BSU25310 --> BSU25310-MONOMER
13000
formation_BSU29140-MONOMER
protein_BSU29140 --> BSU29140-MONOMER
13001
formation_BSU34880-MONOMER
protein_BSU34880 --> BSU34880-MONOMER
13002
formation_BSU19630-MONOMER
protein_BSU19630 --> BSU19630-MONOMER
13003
formation_BSU38460-MONOMER
protein_BSU38460 --> BSU38460-MONOMER
13004
formation_BSU13730-MONOMER
protein_BSU13730 --> BSU13730-MONOMER
13005
formation_BSU39920-MONOMER
protein_BSU39920 

13275
formation_BSU30560-MONOMER
protein_BSU30560 --> BSU30560-MONOMER
13276
formation_BSU01530-MONOMER
protein_BSU01530 --> BSU01530-MONOMER
13277
formation_BSU34920-MONOMER
protein_BSU34920 --> BSU34920-MONOMER
13278
formation_BSU13740-MONOMER
protein_BSU13740 --> BSU13740-MONOMER
13279
formation_BSU27710-MONOMER
protein_BSU27710 --> BSU27710-MONOMER
13280
formation_BSU13140-MONOMER
protein_BSU13140 --> BSU13140-MONOMER
13281
formation_BSU27030-MONOMER
protein_BSU27030 --> BSU27030-MONOMER
13282
formation_BSU21900-MONOMER
protein_BSU21900 --> BSU21900-MONOMER
13283
formation_BSU11690-MONOMER
protein_BSU11690 --> BSU11690-MONOMER
13284
formation_BSU06720-MONOMER
protein_BSU06720 --> BSU06720-MONOMER
13285
formation_CPLX-8648
protein_BSU39760 --> CPLX-8648
13286
formation_CPLX8J2-171
protein_BSU35080 --> CPLX8J2-171
13287
formation_BSU30550-MONOMER
protein_BSU30550 --> BSU30550-MONOMER
13288
formation_BSU14610-MONOMER
protein_BSU14610 --> BSU14610-MONOMER
13289
formation_BSU37680-MONOM

formation_BSU33420-MONOMER
protein_BSU33420 --> BSU33420-MONOMER
13615
formation_BSU11640-MONOMER
protein_BSU11640 --> BSU11640-MONOMER
13616
formation_BSU36510-MONOMER
protein_BSU36510 --> BSU36510-MONOMER
13617
formation_BSU38060-MONOMER
protein_BSU38060 --> BSU38060-MONOMER
13618
formation_BSU37320-MONOMER
protein_BSU37320 --> BSU37320-MONOMER
13619
formation_BSU03330-MONOMER
protein_BSU03330 --> BSU03330-MONOMER
13620
formation_CPLX000-61
protein_BSU24030 + protein_BSU24040 + protein_BSU24050 + protein_BSU24060 --> CPLX000-61
13621
formation_CPLX000-62
protein_BSU24030 + protein_BSU24040 + protein_BSU24050 + protein_BSU24060 --> CPLX000-62
13622
formation_CPLX000-63
protein_BSU24030 + protein_BSU24040 + protein_BSU24050 + protein_BSU24060 --> CPLX000-63
13623
formation_BSU12840-MONOMER
protein_BSU12840 --> BSU12840-MONOMER
13624
formation_BSU25420-MONOMER
protein_BSU25420 --> BSU25420-MONOMER
13625
formation_BSU03010-MONOMER
protein_BSU03010 --> BSU03010-MONOMER
13626
formation_BSU

### 5) Add dummy reaction to model and unmodeled_protein_fraction

Includes the transcription, translation, complex_formation, and metabolic reaction. Sequence based on prevelance of each codon found in *E. coli*.
 - Required
     * [**codon_usage.csv**](http://openwetware.org/wiki/Escherichia_coli/Codon_usage) (codon prevelance)

In [12]:
seq = "ATG"
codons = pandas.read_csv(join(flat_files.ecoli_files_dir, "codon_usage.csv"), index_col=0)
for codon, row in codons.iterrows():
    if row.amino_acid == "Stop":
        continue
    seq += codon * int(row.per_1000 // 3)  # want roughly 300 aa
# get the most used stop codon
seq += codons[codons.amino_acid == "Stop"].sort_values("per_1000").index[-1]
building.add_dummy_reactions(me, seq, update=True)

# dummy proteins can be used to catalyze orphan reactions. This
# ensures that orphan reactions will not becore favored to fulfil 
# unmodeled protein fraction requirement 
rxn = cobrame.SummaryVariable('dummy_protein_to_mass')
me.add_reactions([rxn])
mass = me.metabolites.protein_dummy.formula_weight / 1000.  # in kDa
rxn.add_metabolites({'protein_biomass': -mass, 'protein_dummy': -1,
                     cobrame.Constraint('unmodeled_protein_biomass'): mass})

In [13]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

13781
transcription_RNA_dummy
220 atp_c + 250 ctp_c + 220 gtp_c + 222 utp_c --> RNA_dummy + 291.715403232 mRNA_biomass + 912 ppi_c
13782
DM_RNA_dummy
RNA_dummy + 291.715403232 mRNA_biomass --> 
13783
translation_dummy
0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_dummy + 1.36212620027435*(mu + 0.3915)/mu atp_c + 1.36212620027435*(mu + 0.3915)/mu h2o_c + 1.74469020314338*(mu + 0.3915)/mu mRNA_biomass + met__L_c --> 1.36212620027435*(mu + 0.3915)/mu adp_c + 1.31577503429355*(mu + 0.3915)/mu amp_c + 1.49519890260631*(mu + 0.3915)/mu cmp_c + 1.31577503429355*(mu + 0.3915)/mu gmp_c + 1.36212620027435*(mu + 0.3915)/mu h_c + 1.36212620027435*(mu + 0.3915)/mu pi_c + 0.14921134 protein_biomass + protein_dummy + 1.3277366255144*(mu + 0.3915)/mu ump_c
13784
formation_CPLX_dummy
protein_dummy --> CPLX_dummy
13785
dummy_protein_to_mass
0.14921134 protein_biomass + protein_dummy --> 0.14921134 unmodeled_protein_biomass


### 6) Assocated Complexes and build Metabolic Reactions 
- Required
    * **enzyme_reaction_association.txt**
    * **reactions.txt** (gives reaction name, reversiblity, source and whether reaction is spontaneous)


In [14]:
# associate reaction id with the old ME complex id (including modifications)
rxn_to_cplx_dict = flat_files.get_reaction_to_complex(m_model)
rxn_info = flat_files.get_reaction_info_frame('reactions.txt')

# Required to add dummy reaction as spontaneous reaction
rxn_info = rxn_info.append(pandas.Series({'description': 'dummy reaction', 'is_reversible': 0,
                                          'is_spontaneous':1}, name='dummy_reaction'))

building.add_reactions_from_stoichiometric_data(me, rxn_to_cplx_dict, rxn_info, update=True)

In [15]:
rxn_info

description  \
#name                                                               
23CN2P1         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P2         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P3         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P4         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
26DPAi                                      Dipicolinate_synthase   
2HXMPt6         2__hydroxymethyl_phenol_transport_inout_via_pr...   
2PGLYCt6        2_Phosphoglycolate_transport_inout_via_proton_...   
2PGt6           D_Glycerate_2_phosphate_transport_inout_via_pr...   
2S6HCCi         2_succinyl_6_hydroxy_2_4_cyclohexadiene_1_carb...   
3AMBAt2           3_aminobutyrate_transport_in_via_proton_symport   
3AMPt6                  3__AMP_transport_inout_via_proton_symport   
3CMPt6                     3__CMP_transport_in_via_proton_symport   
3GMPt6          Guanosine_3__phsophate_transport_inout_via_pro...   
3NUCLE1                                  3__nucleotidase__3__AMP_   
3NUCLE2                                  3__nucleotidase__3__UMP_   
3NUCLE3                                  3__nucleotidase__3__cMP_   
3NUCLE4                  3__nucleotidase__guanosine_3__phosphate_   
3PGt6           3_Phospho_D_glycerate_transport_inout_via_prot...   
3UMPt6                     3__UMP_transport_in_via_proton_symport   
5MTRt2          5_Methylthio_D_ribose_transport_inout_via_prot...   
6PGCt6          6_Phospho_D_gluconate_transport_inout_via_prot...   
AAMYL_1                                             Alpha_amylase   
AB6PGH                         Arbutin_6-phosphate_glucohydrolase   
ABTA                                 4-aminobutyrate_transaminase   
ABTt_1               L_arabinitol_transport_via_passive_diffusion   
ABUTD                            Aminobutyraldehyde_dehydrogenase   
MACCOAT                               2-Methylacetyl-CoA_thiolase   
ACACT1r                            Acetyl-CoA_C-acetyltransferase   
ACACT2r           Acetyl-CoA_C-acyltransferase_(butanoyl-CoA)_(r)   
ACACT3r           Acetyl-CoA_C-acyltransferase_(hexanoyl-CoA)_(r)   
...                                                           ...   
URAt2                      Uracil_transport_in_via_proton_symport   
URCN                                                    Urocanase   
UREA                                                       Urease   
UREAt                     Urea_transport_via_facilitate_diffusion   
URIC                                                      Uricase   
UMPK                                                   UMP_kinase   
URIDK2r_copy1                             Uridylate_kinase_(dUMP)   
URIDK2r_copy2                             Uridylate_kinase_(dUMP)   
URIK1                                 Uridine_kinase__ATPUridine_   
URIK2                                Uridine_kinase_(GTP:Uridine)   
URIK3                                Uridine_kinase_(ITP:Uridine)   
URIt2                     Uridine_transport_in_via_proton_symport   
VALDHr                                       Valine_dehydrogenase   
VALTA                                         Valine_transaminase   
VALt2r           L_valine_reversible_transport_via_proton_symport   
X00002                      Lumped_reaction_for_synthesis_of_pime   
HXAND                                  Hypoxanthine_dehydrogenase   
XAND                                       Xanthine_dehydrogenase   
XANt2                    Xanthine_transport_in_via_proton_symport   
XPPT                           Xanthine_phosphoribosyltransferase   
XTSNt2                 Xanthosine_transport_in_via_proton_symport   
XYL14BASE                               Xylan_1_4_beta_xylosidase   
XYLI1                                            Xylose_isomerase   
XYLI2                                            Xylose_isomerase   
XYLK                                                 Xylulokinase   
XYLt2                    D-xylose_transport_in_via_p

In [16]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

13786
23CN2P1_REV_BSU07840-MONOMER
3amp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23camp_c + h2o_c
13787
23CN2P1_FWD_BSU07840-MONOMER
23camp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3amp_c + h_c
13788
23CN2P2_REV_BSU07840-MONOMER
3ump_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23cump_c + h2o_c
13789
23CN2P2_FWD_BSU07840-MONOMER
23cump_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3ump_c + h_c
13790
23CN2P3_REV_BSU07840-MONOMER
3cmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23ccmp_c + h2o_c
13791
23CN2P3_FWD_BSU07840-MONOMER
23ccmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3cmp_c + h_c
13792
23CN2P4_REV_BSU07840-MONOMER
3gmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23cgmp_c + h2o_c
13793
23CN2P4_FWD_BSU07840-MONOMER
23cgmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3gmp_c + h_c
13794
26DPAi_FWD_CPLX8J2-80
23dhdp_c + 4.27350427350427e-6*mu CPLX8J2-80 + nad_c --> DPA_c + h_c + nadh_c
13795


14148
CAT_FWD_BSU38630-MONOMER
4.27350427350427e-6*mu BSU38630-MONOMER + 2.0 h2o2_c --> 2.0 h2o_c + o2_c
14149
CAt4_REV_CPLX8J2-142
4.27350427350427e-6*mu CPLX8J2-142 + ca2_e + h_c --> ca2_c + h_e
14150
CAt4_FWD_CPLX8J2-142
4.27350427350427e-6*mu CPLX8J2-142 + ca2_c + h_e --> ca2_e + h_c
14151
CBL2abc_FWD_CPLX000-10
4.27350427350427e-6*mu CPLX000-10 + atp_c + cbl2_e + h2o_c --> adp_c + cbl2_c + h_c + pi_c
14152
CBPS_FWD_CPLX8J2-6
4.27350427350427e-6*mu CPLX8J2-6 + 2.0 atp_c + gln__L_c + h2o_c + hco3_c --> 2.0 adp_c + cbp_c + glu__L_c + 2.0 h_c + pi_c
14153
CBPS_FWD_CPLX8J2-5
4.27350427350427e-6*mu CPLX8J2-5 + 2.0 atp_c + gln__L_c + h2o_c + hco3_c --> 2.0 adp_c + cbp_c + glu__L_c + 2.0 h_c + pi_c
14154
CD2abc1_FWD_BSU13850-MONOMER
4.27350427350427e-6*mu BSU13850-MONOMER + atp_c + cd2_c + h2o_c --> adp_c + cd2_e + h_c + pi_c
14155
CD2abc1_FWD_BSU33490-MONOMER
4.27350427350427e-6*mu BSU33490-MONOMER + atp_c + cd2_c + h2o_c --> adp_c + cd2_e + h_c + pi_c
14156
CD2t4_FWD_BSU26650-MONOMER
4.

FDMO1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + eths_c + fmnRD_c + o2_c --> acald_c + fmn_c + h2o_c + h_c + so3_c
14482
FDMO2_1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + buts_c + fmnRD_c + o2_c --> btal_c + fmn_c + h2o_c + h_c + so3_c
14483
FDMO3_1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + fmnRD_c + hexs_c + o2_c --> fmn_c + h2o_c + h_c + hxal_c + so3_c
14484
FDMO4_1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + fmnRD_c + o2_c + taur_c --> amacald_c + fmn_c + h2o_c + h_c + so3_c
14485
FDMO5_1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + fmnRD_c + o2_c + sula_c --> fmn_c + glx_c + h2o_c + h_c + so3_c
14486
FDMO6_1_FWD_BSU08860-MONOMER
4.27350427350427e-6*mu BSU08860-MONOMER + fmnRD_c + istnt_c + o2_c --> fmn_c + gcald_c + h2o_c + h_c + so3_c
14487
FE2abc_FWD_CPLX8J2-113
4.27350427350427e-6*mu CPLX8J2-113 + atp_c + fe2_e + h2o_c --> adp_c + fe2_c + h_c + pi_c
14488
FE3t_FWD_CPLX000-17
4.2735

LAAL10_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + atp_c + 2.0 thr__L_c --> adp_c + h_c + pi_c + thr_L_thr__L_c
14815
LAAL11_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + ala__L_c + atp_c + val__L_c --> adp_c + ala_L_val__L_c + h_c + pi_c
14816
LAAL12_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + atp_c + ser__L_c + val__L_c --> adp_c + h_c + pi_c + ser_L_val__L_c
14817
LAAL13_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + atp_c + gly_c + leu__L_c --> adp_c + gly_leu__L_c + h_c + pi_c
14818
LAAL14_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + atp_c + leu__L_c + ser__L_c --> adp_c + h_c + pi_c + ser_L_leu__L_c
14819
LAAL15_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + ala__L_c + atp_c + leu__L_c --> adp_c + ala_L_leu__L_c + h_c + pi_c
14820
LAAL16_FWD_BSU37710-MONOMER
4.27350427350427e-6*mu BSU37710-MONOMER + atp_c + leu__L_c + thr__L_c --> adp_c + h_c + pi_c + thr_L_leu__L_c
14821
LAAL

3php_c + 4.27350427350427e-6*mu CPLX8J2-181 + h_c + nadh_c --> 3pg_c + nad_c
15097
PGCD_FWD_CPLX8J2-181
3pg_c + 4.27350427350427e-6*mu CPLX8J2-181 + nad_c --> 3php_c + h_c + nadh_c
15098
GND_REV_BSU23860-MONOMER
4.27350427350427e-6*mu BSU23860-MONOMER + co2_c + nadph_c + ru5p__D_c --> 6pgc_c + nadp_c
15099
GND_FWD_BSU23860-MONOMER
6pgc_c + 4.27350427350427e-6*mu BSU23860-MONOMER + nadp_c --> co2_c + nadph_c + ru5p__D_c
15100
BGLA1_FWD_BSU38560-MONOMER
6pgg_c + 4.27350427350427e-6*mu BSU38560-MONOMER + h2o_c --> g6p_c + glc__D_c
15101
BGLA1_FWD_BSU40110-MONOMER
6pgg_c + 4.27350427350427e-6*mu BSU40110-MONOMER + h2o_c --> g6p_c + glc__D_c
15102
PGI_REV_BSU31350-MONOMER
4.27350427350427e-6*mu BSU31350-MONOMER + f6p_c --> g6p_c
15103
PGI_FWD_BSU31350-MONOMER
4.27350427350427e-6*mu BSU31350-MONOMER + g6p_c --> f6p_c
15104
PGK_REV_BSU33930-MONOMER
13dpg_c + 4.27350427350427e-6*mu BSU33930-MONOMER + adp_c --> 3pg_c + atp_c
15105
PGK_FWD_BSU33930-MONOMER
3pg_c + 4.27350427350427e-6*mu BSU33930

15319
SUCBZL_FWD_BSU30790-MONOMER
4.27350427350427e-6*mu BSU30790-MONOMER + atp_c + coa_c + sucbz_c --> amp_c + ppi_c + sbzcoa_c
15320
SUCBZS_FWD_BSU30780-MONOMER
2shchc_c + 4.27350427350427e-6*mu BSU30780-MONOMER --> h2o_c + sucbz_c
15321
SUCCt2r_REV_BSU07570-MONOMER
4.27350427350427e-6*mu BSU07570-MONOMER + h_c + succ_c --> h_e + succ_e
15322
SUCCt2r_FWD_BSU07570-MONOMER
4.27350427350427e-6*mu BSU07570-MONOMER + h_e + succ_e --> h_c + succ_c
15323
SUCCt2r_REV_BSU04470-MONOMER
4.27350427350427e-6*mu BSU04470-MONOMER + h_c + succ_c --> h_e + succ_e
15324
SUCCt2r_FWD_BSU04470-MONOMER
4.27350427350427e-6*mu BSU04470-MONOMER + h_e + succ_e --> h_c + succ_c
15325
SUCD1_REV_CPLX8J2-15
4.27350427350427e-6*mu CPLX8J2-15 + fadh2_c + fum_c --> fad_c + succ_c
15326
SUCD1_FWD_CPLX8J2-15
4.27350427350427e-6*mu CPLX8J2-15 + fad_c + succ_c --> fadh2_c + fum_c
15327
SUCD5_BS_FWD_CPLX8J2-15
4.27350427350427e-6*mu CPLX8J2-15 + fadh2_c + 2.0 h_e + mqn7_c --> fad_c + 2.0 h_c + mql7_c
15328
SUCR_FWD_BSU34

### 7) Incorporate remaining biomass constituents
There are leftover components from the *i*JO1366 biomass equation that either: 
1. have no mechanistic function in the model (glycogen)
2. are cofactors that are regenerated (nad)

Applies demands and coefficients from the *i*JO1366 biomass objective function

In [17]:
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

biomass_constituents = {
    "glycogen_c": -.023 / (me.metabolites.glycogen_c.formula_weight / 1000.),
    "nad_c": -.001831,
    "udcpdp_c": -5.5e-05,
    "coa_c": -0.000576,
    "ribflv_c": -0.000223,
    "nadp_c": -0.000447,
    "mlthf_c": -0.000223,
    "thf_c": -0.000223,
    "10fthf_c": -0.000223
}


rxn = cobrame.SummaryVariable('biomass_constituent_demand')
me.add_reactions([rxn])
rxn.add_metabolites(biomass_constituents)
constituent_mass = sum(me.metabolites.get_by_id(c).formula_weight / 1000. * -v
                     for c, v in biomass_constituents.items())
rxn.lower_bound = mu
rxn.upper_bound = mu
rxn.add_metabolites({me.metabolites.constituent_biomass: constituent_mass})

/home/jt/UCSD/cobrame-master/cobrame/core/model.py:103 UserWarning: Adding ATPM reaction to model
/home/jt/UCSD/cobrame-master/cobrame/core/model.py:86 UserWarning: Adding GAM reaction to model


 #### Lipid components
 Metabolites and coefficients from *i*JO1366 biomass objective function

In [18]:
# Find biomass constituents with 3 numbers followed by a compartment in the BOF
lipid = re.compile('\d{3}_.')
lipid_demand = {}
for key, value in ijo.reactions.BIOMASS_BS_10.metabolites.items():
    if lipid.search(key.id):
        lipid_demand[key.id] = abs(value)
                
for met, requirement in lipid_demand.items():
    component_mass = me.metabolites.get_by_id(met).formula_weight / 1000.
    rxn = cobrame.SummaryVariable('Demand_' + met)
    me.add_reactions([rxn])
    rxn.add_metabolites({met: -1 * requirement,
                         'lipid_biomass': component_mass * requirement})
    rxn.lower_bound = mu
    rxn.upper_bound = 1000.

# Kdo2lipid4
#requirement = 0.01945  # in mmol/gDW
#met = me.metabolites.get_by_id('kdo2lipid4_e')
#component_mass = met.formula_weight / 1000.
#rxn = cobrame.SummaryVariable('Demand_' + met.id)
#me.add_reactions([rxn])

#rxn.add_metabolites({met.id : -1.*requirement,
#                     'lipid_biomass': component_mass * requirement})
#rxn.lower_bound = mu
#rxn.upper_bound = mu

In [19]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

15486
ATPM
atp_c + h2o_c --> adp_c + h_c + pi_c
15487
GAM
34.98 atp_c + 34.98 h2o_c --> 34.98 adp_c + 34.98 h_c + 34.98 pi_c
15488
biomass_constituent_demand
0.000223 10fthf_c + 0.000576 coa_c + 0.14185219494685478 glycogen_c + 0.000223 mlthf_c + 0.001831 nad_c + 0.000447 nadp_c + 0.000223 ribflv_c + 0.000223 thf_c + 5.5e-05 udcpdp_c --> 0.025423944002581 constituent_biomass


#### DNA Demand Requirements
Added based on growth rate dependent DNA levels as in [O'brien EJ et al 2013](https://www.ncbi.nlm.nih.gov/pubmed/24084808)

In [20]:
dna_demand_stoich, dna_demand_bound = ecolime.dna_replication.return_gr_dependent_dna_demand(
    me, me.global_info['GC_fraction'])

dna_replication = cobrame.SummaryVariable("DNA_replication")
me.add_reaction(dna_replication)
dna_replication.add_metabolites(dna_demand_stoich)
dna_biomass = cobrame.Constraint("DNA_biomass")

dna_mw = 0
dna_mw_no_ppi = ecolime.dna_replication.get_dna_mw_no_ppi_dict(me)
for met, value in me.reactions.DNA_replication.metabolites.items():
    if met.id != 'ppi_c':
        dna_mw -= value * dna_mw_no_ppi[met.id.replace('_c','')] / 1000.
        
dna_replication.add_metabolites({dna_biomass: dna_mw})
dna_replication.lower_bound = dna_demand_bound 
dna_replication.upper_bound = dna_demand_bound 


**Note**: From this point forward, executing every codeblock should result in a solveable ME-model

------

## Part 2: Add metastructures to solving ME-model
This includes:
1. ribosome
2. RNA polymerase
3. charged_tRNAs

Sometimes multiple entities can perform the same role. To prevent a combinatorial explosion of possibilities, we can create  "generic" version, where any of those entities can fill in.

In [22]:
for generic, components in generics.generic_dict.items():
    cobrame.GenericData(generic, me, components).create_reactions()

KeyError: 'RsmH_mono'

### 1) Add ribosome
This uses the ribosome composition definition in **ecolime/ribosome.py**

In [ ]:
ecolime.ribosome.add_ribosome(me, verbose=False)

In [ ]:
last = 19652;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 2) Add charged tRNA reactions

The tRNA charging reactions were automatically added when loading the genome from the genbank file. However, the charging reactions still need to be made aware of the tRNA synthetases which are responsible.

Uses **trna_charging.py**

In [ ]:
aa_synthetase_dict = ecolime.trna_charging.amino_acid_trna_synthetase
for data in me.tRNA_data:
    data.synthetase = str(aa_synthetase_dict[data.amino_acid])

Generic charged tRNAs are added to translation reactions via SubreactionData below.

All new data added in this block contained in **ecolime/translation.py**

In [ ]:
ecolime.translation.add_charged_trna_subreactions(me)
for data in me.translation_data:
    data.add_initiation_subreactions(start_codons=translation.translation_start_codons,
                                    start_subreactions=set(translation.initiation_subreactions.keys()))

    data.add_elongation_subreactions(elongation_subreactions=set(translation.elongation_subreactions.keys()))

    data.add_termination_subreactions(translation_terminator_dict=translation.translation_stop_dict)

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 3) Add Transcription Metacomplexes
#### RNA Polymerase

Data for RNA_polymerase composition fround in **ecolime/transcription**

Uses *tu_df* from **TUs_from_ecocyc.txt**, above

In [ ]:
for met in transcription.rna_polymerases:
    rnap_obj = cobrame.RNAP(met)
    me.add_metabolites(rnap_obj)
transcription.add_rna_polymerase_complexes(me, verbose=False)

# associate the correct RNA_polymerase and factors to TUs
sigma_to_rnap_dict = transcription.sigma_factor_complex_to_rna_polymerase_dict
for tu_id in tu_df.index:
    transcription_data = me.process_data.get_by_id(tu_id)
    sigma = tu_df.sigma[tu_id]
    rna_polymerase = sigma_to_rnap_dict[sigma]
    transcription_data.RNA_polymerase = rna_polymerase

#### Degradosome (both for RNA degradation and RNA splicing)

All new data contained in **transcription.py**

In [ ]:
me.add_metabolites([cobrame.Complex('RNA_degradosome')])
data = cobrame.ComplexData('RNA_degradosome', me)
for subunit, value in transcription.rna_degradosome.items():
    data.stoichiometry[subunit] = value
data.create_complex_formation(verbose=False)

# Used for RNA splicing
data = cobrame.SubreactionData('RNA_degradation_machine', me)
data.enzyme = 'RNA_degradosome'

data = cobrame.SubreactionData('RNA_degradation_atp_requirement', me)
# .25 water equivaltent for atp hydrolysis per nucleotide
data.stoichiometry = {'atp_c': -.25, 'h2o_c': -.25, 'adp_c': .25,
                      'pi_c': .25, 'h_c': .25}

transcription.add_rna_splicing(me)

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

------
## Part 3: Add remaining modifications
rRNA modifications handled in *add_ribosome*

### 1) Add complex modifications
*complex_modification_dict* from **protein_modification.text**, above

The rest of the new data contained in **ecolime/modifications.py**

In [ ]:
for complex_id, info in complex_modification_dict.items():
    modifications = {}
    for mod, value in info['modifications'].items():
        # stoichiometry of modification determined in 
        # subreaction_data.stoichiometry
        modifications['mod_' + mod] = abs(value)
    me.process_data.get_by_id(complex_id).subreactions = modifications

# Adds modification data for more complicated enzyme modifications
# (ie, iron sulfur cluster modification)
ecolime.modifications.add_modification_procedures(me)

# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

### 2) Add tRNA mods and asocciate them with tRNA charging reactions
New data from:
1. **ecolime/trna_charging.py** (read via *add_tRNA_modification_procedures()*)
2. **post_transcriptional_modification_of_tRNA.txt** (modification types per tRNA)


In [ ]:
# Add tRNA modifications to ME-model
ecolime.trna_charging.add_trna_modification_procedures(me)

# trna_modifications = {tRNA_id: {modifications: count}}
trna_modifications=flat_files.get_trna_modification_targets()
for trna in trna_modifications:
    for data in me.process_data.query(trna):
        data.subreactions = trna_modifications[trna]

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

---
## Part 4: Add remaining subreactions
### 1) Add translation related subreactions
All new data from **ecolime/translation.py**

In [ ]:
# add the translation subreaction data objects to model
translation.add_translation_subreactions_to_model(me)

# add translation subreaction data to reactions
methionine_cleaved=translation.methionine_cleaved
folding_dict=translation.folding_dict

for data in me.translation_data:
    locus_id = data.id
    if locus_id in methionine_cleaved:
        data.subreactions['N_terminal_methionine_cleavage'] = 1

    for folding_type in folding_dict:
        if locus_id in folding_dict[folding_type]:
            data.subreactions[folding_type] = 1

    # This block was ran above, but should be ran again to 
    # incorporate any subreactions not added previously
    data.add_initiation_subreactions(
        start_codons=translation.translation_start_codons,
        start_subreactions=set(translation.initiation_subreactions.keys()))
    data.add_elongation_subreactions(
        elongation_subreactions=set(translation.elongation_subreactions.keys()))
    data.add_termination_subreactions(
        translation_terminator_dict=translation.translation_stop_dict)

    # add organism specific subreactions associated with peptide processing
    for subrxn in translation.peptide_processing_subreactions:
        data.subreactions[subrxn] = 1

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 2) Add transcription related subreactions
All new data from **ecolime/transcription.py**

In [ ]:
for subreaction in transcription.transcription_subreactions:
    subreaction_data = cobrame.SubreactionData(subreaction, me)
    enzymes = transcription.transcription_subreactions[subreaction]['enzymes']
    subreaction_data.stoichiometry = transcription.transcription_subreactions[subreaction]['stoich']
    subreaction_data.enzyme = enzymes

for transcription_data in me.transcription_data:
    # Assume false if not in tu_df
    rho_dependent = tu_df.rho_dependent.get(transcription_data.id, False)
    rho = 'dependent' if rho_dependent else 'independent'
    stable = 'stable' if transcription_data.codes_stable_rna else 'normal'
    transcription_data.subreactions['Transcription_%s_rho_%s' % (stable,
                                                                 rho)] = 1

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

----
## Part 5: Add in translocation

New data from:
1. **peptide_compartment_and_pathways.txt** (Protein compartment and translocation pathway for each membrane complex)
2. **ecolime/translocation.py** (definitions of each translocation pathway)

In [ ]:
# Add TranslocationData
transloc = pandas.read_csv(join(flat_files.ecoli_files_dir,"peptide_compartment_and_pathways2.txt"),
                           sep='\t', comment="#")
for pathway, info in ecolime.translocation.pathway.items():
    if 'alt' not in pathway:
        transloc_data = cobrame.TranslocationData(pathway + '_translocation', me)
    else:
        transloc_data = cobrame.TranslocationData(pathway.replace('_alt', '_translocation_alt'), me)
    transloc_data.enzyme_dict = info['enzymes']
    transloc_data.keff = info['keff']
    transloc_data.length_dependent_energy = info['length_dependent_energy']
    transloc_data.stoichiometry = info['stoichiometry']

# Associate data and add translocation reactions
ecolime.translocation.add_translocation_pathways(me, transloc, membrane_constraints = False)

# Update stoichiometry of membrane complexes
# new_stoich = {complex_id: protein_w_compartment}
new_stoich = defaultdict(dict)
for cplx, row in transloc.set_index('Complex').iterrows():
    if cplx == 'EG10544-MONOMER':
        continue
    protein = row.Protein.split('(')[0] + '_' + row.Protein_compartment
    value = me.process_data.get_by_id(cplx).stoichiometry['protein_' + row.Protein.split('(')[0]]
    new_stoich[cplx]['protein_' + protein] = float(value)

for cplx, stoich in new_stoich.items():
    complex_data = me.process_data.get_by_id(cplx)
    for met, value in stoich.items():
        complex_data.stoichiometry.pop(met[0:13])
        complex_data.stoichiometry[met] = value
        complex_data.formation.update()
    # Complex ids in protein compartment file doesn't include mods
    # Some have multiple alternative modifications so must loop through these
    for complex_data in me.process_data.query(cplx + '_mod_'):
        for met, value in stoich.items():
            complex_data.stoichiometry.pop(met[0:13])
            complex_data.stoichiometry[met] = value
            complex_data.formation.update()

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

---
## Part 6: Add Cell Wall Components
All new data from **ecolime/translocation.py**

In [ ]:
compartment_dict = {}
for prot, compartment in transloc.set_index('Protein').Protein_compartment.to_dict().items():
    compartment_dict[prot.split('(')[0]] = compartment

#### Add lipid modification SubreactionData

In [ ]:
lipid_modifications = ecolime.translocation.lipid_modifications

for lipid in lipid_modifications:
    data = cobrame.SubreactionData('mod_' + lipid, me)
    data.stoichiometry = {lipid: -1, 'g3p_c': 1}
    data.enzyme = ['Lgt_MONOMER', 'LspA_MONOMER']
    # The element contribution is based on the lipid involved in the 
    # modification, so calculate based on the metabolite formula
    data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pg160_p', me)
data.stoichiometry = {'pg160_p': -1, '2agpg160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pe160_p', me)
data.stoichiometry = {'pe160_p': -1, '2agpe160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()
    
ecolime.translocation.add_lipoprotein_formation(me, compartment_dict, 
                                                membrane_constraints=False)

#### Correct complex formation IDs if they contain lipoproteins

In [ ]:
for gene in ecolime.translocation.lipoprotein_precursors.values():
    compartment = compartment_dict.get(gene)
    for rxn in me.metabolites.get_by_id('protein_' + gene + '_' + compartment).reactions:
        if isinstance(rxn, cobrame.ComplexFormation):
            data = me.process_data.get_by_id(rxn.complex_data_id)
            value = data.stoichiometry.pop('protein_' + gene + '_' + compartment)
            data.stoichiometry['protein_' + gene + '_lipoprotein' + '_' + compartment] = value
            rxn.update()

#### Braun's lipoprotein demand
Metabolites and coefficients as defined in [Liu et al 2014](http://bmcsystbiol.biomedcentral.com/articles/10.1186/s12918-014-0110-6)

In [ ]:
rxn = cobrame.SummaryVariable('core_structural_demand_brauns')
met1 = me.metabolites.get_by_id('murein5px4p_p')
met1_mass = met1.formula_weight / 1000.
met2 = me.metabolites.get_by_id('protein_b1677_lipoprotein_Outer_Membrane')
me.add_reactions([rxn])
# biomass of lipoprotein accounted for in translation and lipid modification
rxn.add_metabolites({met1 : -0.013894, met2: -0.003597, 'peptidoglycan_biomass':(0.013894 * met1_mass)},
                    combine=False)
rxn.lower_bound = mu
rxn.upper_bound = mu

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

-----
## Part 7: Set keffs

Either entirely based on SASA or using fit keffs from [Ebrahim et al 2016](https://www.ncbi.nlm.nih.gov/pubmed/27782110?dopt=Abstract)

In [2]:
keff_list = []
keffs = flat_files.get_reaction_keffs(me, verbose=True)
for reaction_id, keff in keffs.items():
    if keff > 3000:
        keff = 3000.
    elif keff < .01:
        keff = .01
    keff_list.append(keff)
    me.reactions.get_by_id(reaction_id).keff = keff
    me.reactions.get_by_id(reaction_id).update()

# Keffs that were not set in the above block
me.process_data.N_terminal_methionine_cleavage.keff = 1339.4233102860871
me.process_data.peptide_deformylase_processing.keff = 1019.5963333345715
me.reactions.get_by_id('GLUTRR_FWD_CPLX0-3741').keff = 3000 # 3269.0108007383374
me.process_data.fmet_addition_at_START.keff = 1540.4356849968603
me.process_data.ribosome_recycler.keff = 1059.6910912619182
me.process_data.UAG_PrfA_mono_mediated_termination.keff = 1721.7910609284945
me.process_data.UGA_PrfB_mono_mediated_termination.keff = 1700.2966587695353
me.process_data.UAA_generic_RF_mediated_termination.keff = 1753.4238515034572

NameError: name 'flat_files' is not defined

-----
## Part 8: Model updates and corrections

In [ ]:
# Add reaction subsystems from iJO to model
for rxn in ijo.reactions:
    if rxn.id in me.process_data:
        data = me.process_data.get_by_id(rxn.id)
    else:
        continue
    for r in data.parent_reactions:
        r.subsystem = rxn.subsystem

#### Corrections and final updates

In [ ]:
ecolime.corrections.correct_reaction_stoichiometries(me, join(flat_files.ecoli_files_dir, 
                                                              'iJL1678b_model_changes.xlsx'))
# RNA_dummy, TU_b3247, TU_b3705 do not have RNAP, this is set as the most common RNAP
for data in me.transcription_data:
    if len(data.RNA_polymerase) == 0:
        data.RNA_polymerase = 'RNAP70-CPLX'
        
# If lower_bound open, model feeds G6P into EDD
me.reactions.EX_pqq_e.lower_bound = 0
me.reactions.EX_pqq_e.upper_bound = 0

# cobalamin is not in glucose M9 media
me.reactions.EX_cbl1_e.lower_bound = 0

me.process_data.PPKr.lower_bound = 0.
me.process_data.PPKr.update_parent_reactions()
    

# This enyzme is involved in catalyzing this reaction
sub = cobrame.SubreactionData('EG12450-MONOMER_activity', me)
sub.enzyme = 'EG12450-MONOMER'
me.process_data.NHFRBO.subreactions['EG12450-MONOMER_activity'] = 1

#### Add enzymatic coupling for "carriers"
These are enzyme complexes that act as metabolites in a metabolic reaction (i.e. are metabolites in iJO1366)

In [ ]:
for data in me.stoichiometric_data:
    if data.id == 'dummy_reaction':
        continue
        
    for met, value in data.stoichiometry.items():
        if not isinstance(me.metabolites.get_by_id(met), cobrame.Complex) or value > 0:
            continue
            
        subreaction_id = met + '_carrier_activity'
        if subreaction_id not in me.process_data:           
            sub = cobrame.SubreactionData(met + '_carrier_activity', me)
            sub.enzyme = met
        data.subreactions[subreaction_id] = abs(value)

----
## Part 9: Update and save

In [ ]:
me.reactions.dummy_reaction_FWD_SPONT.objective_coefficient = 1.
me.reactions.EX_glc__D_e.lower_bound = -1000
me.reactions.EX_o2_e.lower_bound = -1000
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

In [ ]:
me.update()
me.prune()

### Add remaining complex formulas and compartments to model

In [ ]:
# Update a second time to incorporate all of the metabolite formulas corectly
for r in me.reactions.query('formation_'):
    r.update()

# Update complex formulas
df = pandas.read_table(join(flat_files.ecoli_files_dir, 'modification.txt'),
                            names=['mod', 'formula','na'])
df = df.drop('na', axis=1).set_index('mod').dropna(how='any')
modification_formulas = df.T.to_dict()
formulas.add_remaining_complex_formulas(me, modification_formulas)

me.metabolites.get_by_id('CPLX0-782_mod_1:2fe2s_mod_1:4fe4s').formula = 'C3164Fe6H5090N920O920S50'
me.metabolites.get_by_id('EG50003-MONOMER_mod_pan4p_mod_lipo').formula = 'C387H606N95O142PS4'
# Update reactions affected by formula update 
for r in me.reactions.query('_mod_lipo'):
    r.update()
for r in me.reactions.query('_mod_glycyl'):
    r.update()
    
# add metaboolite compartments
compartments.add_compartments_to_model(me)

In [ ]:
n_genes = len(me.metabolites.query(re.compile('RNA_b[0-9]')))
print("number of genes in the model %d (%.2f%%)" % (n_genes, n_genes * 100. / (1678)))

In [ ]:
with open("./me_models/iJL1678b.pickle", "wb") as outfile:
    pickle.dump(me, outfile)

In [ ]:
save_json_me_model(me, './me_models/iJL1678b.json')